In [1]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import seaborn as sns
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

from datetime import datetime
import math
import warnings
warnings.filterwarnings('ignore')

In [ ]:
#Insights from the data
'''
due dates are often missing.
'''

In [ ]:
#Things that need definition
'''
What is the main outcome measure(s)  E.g. assignment latest_graded_date?  The 
'''

In [ ]:
#Hypotheses
'''
Does assignment type = None have an effect on late grades
'''

In [2]:
#data given for the interview
df = pd.read_csv('interview_dataset.csv')

In [3]:
df.head()

term term_start_date term_end_date     class_name     assignment_name  \
0  Fall 2022       8/21/2022    12/13/2022  CHEM 1113-300   Recitation Week 2   
1  Fall 2022       8/21/2022    12/13/2022  CHEM 1113-314   Recitation Week 2   
2  Fall 2022       8/21/2022    12/13/2022  CHEM 1113-300  Recitation Week 14   
3  Fall 2022       8/21/2022    12/13/2022  CHEM 1113-314  Recitation Week 14   
4  Fall 2022       8/21/2022    12/13/2022  CHEM 1113-300  Recitation Week 13   

  assignment_type assignment_posted_date assignment_due_date  \
0            none               8/3/2022                 NaN   
1            none               8/3/2022                 NaN   
2            none               8/3/2022                 NaN   
3            none               8/3/2022                 NaN   
4            none               8/3/2022                 NaN   

  assignment_latest_graded_date assignment_earliest_graded_date  
0                    12/12/2022                        9/6/2022  
1                     9/12/2022                        9/9/2022  
2                    12/14/2022                       12/5/2022  
3                     12/8/2022                       12/6/2022  
4                     12/9/2022                      11/28/2022

In [4]:
df.shape

(47866, 10)

In [5]:
#First, transform the date fields into date type
cols = df.columns
for c in cols:
    if 'date' in c:
        df[c] = pd.to_datetime(df[c])


'''
between (1) the number of days between an assignment’s due date and 
the start of the term and (2) the number of days between the assignment’s latest graded date and the assignment’s due date. Use any method you like to quantify the relationship (or lack of one). 
Be prepared to walk us through your method, explain why you chose the method you did, 
and why you do or do not think the relationship (or lack of one) is meaningful/significant.
'''

df["due_Weekday"] = df["assignment_due_date"].apply(lambda x: datetime.strftime(x, '%A') if not(pd.isnull(x)) else None) 
df["due_Day_Number"] = df["assignment_due_date"].apply(lambda x: str(datetime.weekday(x)) if not(pd.isnull(x)) else None)

#Also, calculate durations from maybe assignment posted to 
df['graded_time_diff'] = df.assignment_latest_graded_date - df.assignment_earliest_graded_date
df['duedate_time_diff'] = df.assignment_latest_graded_date - df.assignment_due_date
df['termstart_time_diff'] = df.assignment_due_date - df.term_start_date
df['termendGDD_time_diff'] = df.term_end_date - df.assignment_latest_graded_date

df['graded_time_diff'] = df['graded_time_diff'].dt.days
df['duedate_time_diff'] = df['duedate_time_diff'].dt.days
df['termstart_time_diff'] = df['termstart_time_diff'].dt.days
df['termendGDD_time_diff'] = df['termendGDD_time_diff'].dt.days

# df['gtd_gt7'] = df['graded_time_diff'] > 7
# df['gtd_gt50'] = df['graded_time_diff'] > 50
# df['gtd_gt100'] = df['graded_time_diff'] > 100
# df['log_graded_time_diff'] = np.log(df['graded_time_diff']+1)
        
#Also, replace assignment_due_date from NaN to none, to match assignment type?  Or maybe recode both of them into something else.
df.assignment_due_date = df.assignment_due_date.fillna('none')



In [6]:
#Maybe make two new variables out of class_name: major (e.g. CHEM) and level (e.g. 1000)
df['subject'] = ''
df['level'] = ''
df['level2'] = ''
for i in range(len(df.class_name)):
    words = df.class_name[i].split()
    df['subject'][i] = words[0]
    level = words[1].split('-')
    df['level'][i] = level[0]
    df['level2'][i] = level[1]

#Make has_due_date and has_assignment_type boolean variables
df['has_due_date'] = df['assignment_due_date'] != "none"
df['has_assignment_type'] = df['assignment_type'] != "none"

#Can class type be joined with anything in the Scorecard data?

#Combine the online_text_entry types in assignment type

#Maybe wordcloud on assignment names?

In [7]:
df.level = df.level.astype(int)
for i in range(len(df.level)):
    df.level[i] = round(df.level[i],-3)

In [8]:
df['graded_time_diff'].median()

3.0

In [ ]:
df2 = df.copy()
df2 = df2[df2['assignment_type'].isin(['external_tool','none','online_quiz','online_upload'])]
df2 = df2.reset_index(drop=True)

df3 = df.copy()
df3 = df2[df2['assignment_type'].isin(['external_tool'])]
df3 = df3.reset_index(drop=True)

In [ ]:
df.columns

In [9]:
x = df.subject.value_counts()/sum(df2.subject.value_counts())
print(x[0:5])
print(sum(x[0:5]))

NameError: name 'df2' is not defined

In [10]:
class_level = pd.pivot_table(df, values='term', index=['subject'],columns=['level'], aggfunc='count')
class_level

level       1000    2000
subject                 
APPM      2261.0     NaN
ASEN        20.0     NaN
ATOC       357.0     NaN
CHEM     10192.0     NaN
CSCI      3621.0     NaN
EBIO      1279.0     NaN
ECON         NaN  8746.0
MATH      4168.0     NaN
MCDB       373.0     NaN
PHYS     12545.0     NaN
PSYC      1060.0     NaN
WRTG      3244.0     NaN

In [ ]:
df3.head()

In [ ]:
pt1 = pd.pivot_table(df, values='log_graded_time_diff', index=['has_due_date'],columns=['has_assignment_type'], aggfunc='count')#np.mean)#np.sum)'
pt2 = pd.pivot_table(df2, values='gtd_gt7', index=['has_due_date'],columns=['assignment_type'], aggfunc=np.mean)#np.mean)#np.sum)'
pt21 = pd.pivot_table(df2, values='graded_time_diff', index=['has_due_date'],columns=['assignment_type'], aggfunc=np.median)#np.mean)#np.sum)'
pt3 = pd.pivot_table(df, values='graded_time_diff', index=['has_due_date'],columns=['has_assignment_type'], aggfunc=np.median)#np.mean)#np.sum)'

# pt4 = pd.pivot_table(df2, values='gtd_gt50', index=['has_due_date'],columns=['has_assignment_type'], aggfunc=np.mean)#np.mean)#np.sum)'
# pt5 = pd.pivot_table(df2, values='gtd_gt100', index=['has_due_date'],columns=['has_assignment_type'], aggfunc=np.mean)#np.mean)#np.sum)'

In [ ]:
print(pt21)
print(pt3)
# print(pt4)
# print(pt5)

In [ ]:

pt1_df = pd.DataFrame({"Has Assignment Type":["False","False","True","True"],"Has Due Date":["False","True","False","True"], "Count":[14641,3199,4149,25877]})
pt1_df['Probability'] = pt1_df.Count/sum(pt1_df.Count)
pt2_df = pd.DataFrame({"Assignment Type":["external_tool","external_tool","none","none","online_quiz","online_quiz","online_upload","online_upload"],
                       "Has Due Date":["False","True","False","True","False","True","False","True"], 
                       "Probability":[0.27,0.48,.21,.25,.53,.59,.45,.46]})

pt21_df = pd.DataFrame({"Assignment Type":["external_tool","external_tool","none","none","online_quiz","online_quiz","online_upload","online_upload"],
                       "Has Due Date":["False","True","False","True","False","True","False","True"], 
                       "Median GDD":[0.1,7,0.1,0.1,8,13,6,6]})

# pt4_df = pd.DataFrame({"Has Assignment Type":["False","False","True","True"],"Has Due Date":["False","True","False","True"], "Probability":[0.084011,0.069397,0.120029,0.153457]})
# pt5_df = pd.DataFrame({"Has Assignment Type":["False","False","True","True"],"Has Due Date":["False","True","False","True"], "Probability":[0.004781,0.003751,0.011810,0.029872]})

pt3_df = pd.DataFrame({"Has Assignment Type":["False","False","True","True"],"Has Due Date":["False","True","False","True"], "Median":[0.1,0.1,3,7]})

# pt2_df['Count'] = pt1_df['Count']
# pt2_df['CI'] = 1.96 * np.sqrt(pt2_df.Probability*(1-pt2_df.Probability)/pt2_df.Count)

# pt4_df['Count'] = pt1_df['Count']
# pt4_df['CI'] = 1.96 * np.sqrt(pt4_df.Probability*(1-pt4_df.Probability)/pt4_df.Count)

# pt5_df['Count'] = pt1_df['Count']
# pt5_df['CI'] = 1.96 * np.sqrt(pt5_df.Probability*(1-pt5_df.Probability)/pt5_df.Count)


In [ ]:
gt7 = df['gtd_gt7'].mean()
gt50 = df['gtd_gt50'].mean()
gt100 = df['gtd_gt100'].mean()
NDD = 1- df['has_due_date'].mean()
NAT = 1- df['has_assignment_type'].mean()
print('GDD is graded date difference')
print(f'{NDD:.0%} of grades have no due date, so GDD is helpful in that case')
print(f'{NAT:.0%} of grades have no AT')
print(f'{gt7:.0%} of grades had GDD > 7')
print(f'{gt50:.0%} of grades had GDD > 50')
print(f'{gt100:.0%} of grades had GDD > 100')

In [ ]:
# fig = px.scatter(df.sort_values(by='graded_time_diff'),x=df.index,y='graded_time_diff',
#           height=500,width=800,
#           color_discrete_sequence=px.colors.qualitative.Dark24,
#           title = 'Distribution of GDDs',
#           template = 'plotly_white',)

# fig.add_hline(y=7, line_dash="dot",
#               annotation_text="7 days", 
#               annotation_position="top left")
# fig.add_hline(y=50, line_dash="dot",
#               annotation_text="About 1/2 a semester", 
#               annotation_position="top left")
# fig.add_hline(y=100, line_dash="dot",
#               annotation_text="About a semester", 
#               annotation_position="top left")

# fig.update_traces(opacity=.8)
# fig.update_traces(marker={'size': 3})
# fig.update_xaxes(showticklabels=False,title='')
# fig.update_yaxes(title='Graded Date Difference in Days')
# fig.show()

In [ ]:
px.scatter(df.sort_values(by='graded_time_diff'),x=df.index,y='log_graded_time_diff',
          height=500,width=500,
          color_discrete_sequence=px.colors.qualitative.Dark24,
          title = 'Distribution of differences between earliest and latest grade dates',
          template = 'plotly_white',)

In [ ]:
fig = px.bar(pt1_df,x='Has Assignment Type',y='Probability',
      color='Has Due Date', #barmode='group',
      height=500,width=500,
      color_discrete_sequence=px.colors.qualitative.Dark24,
      template = 'plotly_white',
      title="Does the assignment have a Type and a Due Date?")

fig.update_yaxes(tickformat='.1%',title="Percentage")
fig.show()

In [ ]:
pt200 = pd.pivot_table(df2, values='log_graded_time_diff', index=['has_due_date'],columns=['assignment_type'], aggfunc='count')#np.mean)#np.sum)'
pt200/len(df)

In [ ]:
pt200_df = pd.DataFrame({"Assignment Type":["external_tool","external_tool","none","none","online_quiz","online_quiz","online_upload","online_upload"],
                       "Has Due Date":["False","True","False","True","False","True","False","True"], 
                       "Percentage":[.0319,.3541,.3058,.0668,.0254,.0756,.0232,.0695]})

In [ ]:
fig = px.bar(pt200_df,x='Assignment Type',y='Percentage',
      color='Has Due Date',# barmode='group',
      height=500,width=800,
      color_discrete_sequence=px.colors.qualitative.Dark24,
      template = 'plotly_white',
      #error_y="CI",
      title="Percentage that have Due Date by Assignment Type")

fig.update_yaxes(tickformat='.0%')#,range =[0,0.55])#,title='Six-year completion rate')

fig.show()

In [ ]:
#Next, look at who tends to have an assignment type and due date

#Who has an assignment type by due date?
sum1 = pd.DataFrame(df.groupby(['assignment_type'])['assignment_name'].agg('count'))
sum1 = sum1.sort_values(by='assignment_name', ascending=False)
sum1['cum_sum'] = sum1.cumsum()
sum1['cum_perc'] =  round(100*sum1['cum_sum']/sum1['assignment_name'].sum(),1)
sum1['percentage'] = sum1['assignment_name']/sum1['assignment_name'].sum()
sum1 = sum1.loc[['external_tool','none','online_quiz','online_upload']]
sum1
#len(df)*.95

In [ ]:
fig = px.bar(sum1,x=sum1.index,y='percentage',
      #color='Has Due Date', barmode='group',
      height=500,width=800,
      color_discrete_sequence=px.colors.qualitative.Dark24,
      template = 'plotly_white',
      title="Percentage of the top 4 assignment types")

fig.update_yaxes(tickformat='.0%')#,range =[0,0.55])#,title='Six-year completion rate')

fig.show()

In [ ]:
fig = px.bar(pt2_df,x='Assignment Type',y='Probability',
      color='Has Due Date', barmode='group',
      height=500,width=800,
      color_discrete_sequence=px.colors.qualitative.Dark24,
      template = 'plotly_white',
      #error_y="CI",
      title="GDD > 7 days")

fig.update_yaxes(tickformat='.0%')#,range =[0,0.55])#,title='Six-year completion rate')

fig.show()

In [ ]:
fig = px.bar(pt21_df,x='Assignment Type',y='Median GDD',
      color='Has Due Date', barmode='group',
      height=500,width=800,
      color_discrete_sequence=px.colors.qualitative.Dark24,
      template = 'plotly_white',
      #error_y="CI",
      title="Median GDD by Assignment Type and Due Date (True/False)")

#fig.update_yaxes(tickformat='.0%')#,range =[0,0.55])#,title='Six-year completion rate')

fig.show()

In [ ]:
fig = px.bar(pt3_df,x='Has Assignment Type',y='Median',
      color='Has Due Date', barmode='group',
      height=500,width=500,
      color_discrete_sequence=px.colors.qualitative.Dark24,
      template = 'plotly_white',
      #error_y="CI",
      title="Median Graded Date Difference (GDD)")

fig.update_yaxes(range =[0,7.1],title='Median GDD in days')

fig.show()

In [ ]:
fig = px.bar(pt4_df,x='Has Assignment Type',y='Probability',
      color='Has Due Date', barmode='group',
      height=500,width=800,
      color_discrete_sequence=px.colors.qualitative.Dark24,
      template = 'plotly_white',
      #error_y="CI",
      title="Probability latest minus earliest date when any grade was posted was greater than 50 days")

fig.update_yaxes(tickformat='.0%')#,range =[0,0.55])#,title='Six-year completion rate')

fig.show()

In [ ]:
fig = px.bar(pt5_df,x='Has Assignment Type',y='Probability',
      color='Has Due Date', barmode='group',
      height=500,width=800,
      color_discrete_sequence=px.colors.qualitative.Dark24,
      template = 'plotly_white',
      #error_y="CI",
      title="Probability latest minus earliest date when any grade was posted was greater than 100 days")

fig.update_yaxes(tickformat='.1%')#,range =[0,0.55])#,title='Six-year completion rate')

fig.show()

In [ ]:
df.groupby('term').agg('count')
#is there a pattern to the missing data?  Do some date manipulation and look at it by month

In [ ]:
n = 10
c = df.columns[n]
print(c)
x = df[c].value_counts()/sum(df[c].value_counts())
x.sort_index()
x.sort_values()

In [ ]:
df.iloc[1100][7:13]

In [ ]:
#do a graded_time_diff by due_Weekday box plot
fig = px.box(df, x="has_assignment_type", y="log_graded_time_diff",height=600,width=800,color="has_due_date",
             #facet_col='has_assignment_type',#facet_row='has_due_date',
             #category_orders={"due_Weekday": ["Monday", "Tuesday", "Wednesday", "Thursday","Friday","Saturday","Sunday"],
                              #"sex": ["Male", "Female"]
                   color_discrete_sequence=px.colors.qualitative.Dark24,
                   template = 'simple_white',
                             )
fig.show()

In [ ]:
assignment_name_words = {}

for i in range(len(df2.assignment_name)):
    words = df2.assignment_name[i].split()
    for word in words:
        if word in assignment_name_words.keys():
            assignment_name_words[word] += 1
        else:
            assignment_name_words[word] = 1

In [ ]:
sorted(assignment_name_words.items(), key=lambda x: x[1], reverse=True)

In [ ]:
#Some assignment facts
'''
Some assignments are submitted for no grade
Separate midterm and final exams
'''

In [ ]:
most_freq_assg_words = {}

search_key1 = 'omework'
search_key2 = 'hw'
search_key3 = 'HW'
anw_hw = dict(filter(lambda item: search_key1 in item[0] or search_key2 in item[0] or search_key3 in item[0], assignment_name_words.items()))
anw_hw_count = sum(anw_hw.values())

most_freq_assg_words['hw'] = anw_hw_count/len(df2)

print(f'{anw_hw_count/len(df2):.1%} of assignments contain the words homework or HW')
print(anw_hw.keys())


In [ ]:
df2['hw'] = 0
for i in range(len(df2.assignment_name)):
    for k in anw_hw.keys():
        if k in df2.assignment_name[i]:
            df2.hw[i] = 1
            break
            


In [ ]:
search_key1 = 'ecitation'
anw_rec = dict(filter(lambda item: search_key1 in item[0], assignment_name_words.items()))
anw_rec_count = sum(anw_rec.values())

most_freq_assg_words['recitation'] = anw_rec_count/len(df2)

print(f'{anw_rec_count/len(df2):.1%} of assignments contain the word LearningCurve')
print(anw_rec.keys())

In [ ]:
df2['recitation'] = 0
for i in range(len(df2.assignment_name)):
    for k in anw_rec.keys():
        if k in df2.assignment_name[i]:
            df2.recitation[i] = 1
            break


In [ ]:
search_key1 = 'xam'
anw_exam = dict(filter(lambda item: search_key1 in item[0], assignment_name_words.items()))
anw_exam_count = sum(anw_exam.values())

most_freq_assg_words['exam'] = anw_exam_count/len(df2)

print(f'{anw_exam_count/len(df2):.1%} of assignments contain the word MP')
print(anw_exam.keys())

In [ ]:
df2['exam'] = 0
for i in range(len(df2.assignment_name)):
    for k in anw_exam.keys():
        if k in df2.assignment_name[i]:
            df2.exam[i] = 1
            break

In [ ]:
search_key1 = 'uiz'
anw_quiz = dict(filter(lambda item: search_key1 in item[0], assignment_name_words.items()))
anw_quiz_count = sum(anw_quiz.values())

most_freq_assg_words['quiz'] = anw_quiz_count/len(df2)

print(f'{anw_quiz_count/len(df2):.1%} of assignments contain the word Coderunner')
print(anw_quiz.keys())

In [ ]:
df2['quiz'] = 0
for i in range(len(df2.assignment_name)):
    for k in anw_quiz.keys():
        if k in df2.assignment_name[i]:
            df2.quiz[i] = 1
            break

In [ ]:
search_key1 = 'Tut'
search_key2 = 'tut'
# search_key3 = 'idterm'
# search_key4 = 'inal'
# search_key5 = 'pre'
# search_key6 = 'post'
anw_tut = dict(filter(lambda item: search_key1 in item[0] or 
                                    search_key2 in item[0],
                                    # search_key3 not in item[0] and
                                    # search_key4 not in item[0] and
                                    # search_key5 not in item[0] and
                                    # search_key6 not in item[0], 
                       assignment_name_words.items()))
anw_tut_count = sum(anw_tut.values())

most_freq_assg_words['tutorial'] = anw_tut_count/len(df2)

print(f'{anw_tut_count/len(df2):.1%} of assignments contain the word tutorial in some form')
print(anw_tut.keys())

In [ ]:
df2['tutorial'] = 0
for i in range(len(df2.assignment_name)):
    for k in anw_tut.keys():
        if k in df2.assignment_name[i]:
            df2.tutorial[i] = 1
            break

In [ ]:
search_key1 = 'hapt'
search_key2 = 'Ch'
search_key3 = 'ch'
# search_key4 = 'inal'
# search_key5 = 'pre'
# search_key6 = 'post'
anw_chap = dict(filter(lambda item: search_key1 in item[0] or 
                                    search_key2 == item[0] or
                                    search_key3 == item[0],
                                    # search_key4 not in item[0] and
                                    # search_key5 not in item[0] and
                                    # search_key6 not in item[0], 
                       assignment_name_words.items()))
anw_chap_count = sum(anw_chap.values())

most_freq_assg_words['chapter'] = anw_chap_count/len(df2)

print(f'{anw_chap_count/len(df2):.1%} of assignments contain the word chapter in some form')
print(anw_chap.keys())

In [ ]:
df2['chapter'] = 0
for i in range(len(df2.assignment_name)):
    for k in anw_chap.keys():
        if k in df2.assignment_name[i]:
            df2.chapter[i] = 1
            break

In [ ]:
search_key1 = 'ectur'
# search_key2 = 'Ch'
# search_key3 = 'ch'
# search_key4 = 'inal'
# search_key5 = 'pre'
# search_key6 = 'post'
anw_lecture = dict(filter(lambda item: search_key1 in item[0],
                                    # search_key2 == item[0] or
                                    # search_key3 == item[0]
                                    # search_key4 not in item[0] and
                                    # search_key5 not in item[0] and
                                    # search_key6 not in item[0], 
                       assignment_name_words.items()))
anw_lecture_count = sum(anw_lecture.values())

most_freq_assg_words['lecture'] = anw_lecture_count/len(df2)

print(f'{anw_lecture_count/len(df2):.1%} of assignments contain the word lecture in some form')
print(anw_lecture.keys())

In [ ]:
df2['lecture'] = 0
for i in range(len(df2.assignment_name)):
    for k in anw_lecture.keys():
        if k in df2.assignment_name[i]:
            df2.lecture[i] = 1
            break

In [ ]:
for key,value in most_freq_assg_words.items():
    print(f'{key}:{value:.1%}')

print(f'Together, they appear in {sum(most_freq_assg_words.values()):.1%} of assignments')

In [ ]:
df2.columns

In [ ]:
df2['name_sum'] = df2.hw+df2.recitation+df2.exam+df2.quiz+df2.tutorial+df2.chapter+df2.lecture

In [ ]:
df2.name_sum.value_counts()/len(df2)

In [ ]:
'''
These categories account for 85% of all assignments
36% contain two of these words

'''

In [ ]:
df2[df2.has_due_date == False].assignment_name

In [ ]:
'''
so, maybe I should compare key words by whether something has a due date or not
'''

In [ ]:
df2[(df2.assignment_type=='external_tool') & (df2.has_due_date == False) & (df2.assignment_name == 'Final Exam')]

In [ ]:
#df2.hw+df2.recitation+df2.exam+df2.quiz+df2.tutorial+df2.chapter+df2.lecture
pt300 = pd.pivot_table(df2, values='hw', index=['has_due_date'],columns=['assignment_type'], aggfunc=np.mean)#np.mean)#np.sum)'
pt300

In [ ]:
pt300 = pd.pivot_table(df2, values='recitation', index=['has_due_date'],columns=['assignment_type'], aggfunc=np.mean)#np.mean)#np.sum)'
pt300

In [ ]:
#df2.hw+df2.recitation+df2.exam+df2.quiz+df2.tutorial+df2.chapter+df2.lecture
pt300 = pd.pivot_table(df2, values='exam', index=['has_due_date'],columns=['assignment_type'], aggfunc=np.mean)#np.mean)#np.sum)'
pt300

In [ ]:
#df2.hw+df2.recitation+df2.exam+df2.quiz+df2.tutorial+df2.chapter+df2.lecture
pt300 = pd.pivot_table(df2, values='quiz', index=['has_due_date'],columns=['assignment_type'], aggfunc=np.mean)#np.mean)#np.sum)'
pt300

In [ ]:
#df2.hw+df2.recitation+df2.exam+df2.quiz+df2.tutorial+df2.chapter+df2.lecture
pt300 = pd.pivot_table(df2, values='tutorial', index=['has_due_date'],columns=['assignment_type'], aggfunc=np.mean)#np.mean)#np.sum)'
pt300

In [ ]:
#df2.hw+df2.recitation+df2.exam+df2.quiz+df2.tutorial+df2.chapter+df2.lecture
pt300 = pd.pivot_table(df2, values='chapter', index=['has_due_date'],columns=['assignment_type'], aggfunc=np.mean)#np.mean)#np.sum)'
pt300

In [ ]:
#df2.hw+df2.recitation+df2.exam+df2.quiz+df2.tutorial+df2.chapter+df2.lecture
pt300 = pd.pivot_table(df2, values='lecture', index=['has_due_date'],columns=['assignment_type'], aggfunc=np.mean)#np.mean)#np.sum)'
pt300

In [ ]:
#Assignment Description
'''
Data Presentation (30 minutes - 20 minute presentation followed by 10 minute Q&A)

Presentation about a data request (please see attachment)
The Prompt: The Academic Technology group is working on a project aimed to improve the student experience with grades in Canvas and to better understand faculty grading practices. 

You are provided with a list of several courses and associated Canvas grading data. Leadership wants to take a data-informed approach and has asked you to help them understand 
what grading practices look like in Canvas courses and to develop at least one recommendation for improving student experience with grading in Canvas based on the data. 
Please prepare a 20-minute presentation addressing the following:
    How would you approach analyzing this data? 
    What questions would you ask about the data to help you analyze it?
    What insights could you derive from the data? Create at least one visualization that shows something interesting or surprising.
    What story (or stories) does this tell? 
    What’s at least one recommendation you would you make to campus leadership to improve the student experience with grades in Canvas?

 
Explanation for Sample data set: This dataset is a list of Canvas assignments and some associated data across several courses and two different semesters. 
Each row represents a distinct Canvas assignment. Here are explanations of some of the columns:
    assignment posted date: When the assignment was first published in the Canvas course
    assignment due date: The due date given to the assignment in Canvas
    term start/end date: The date when the corresponding academic term began/ended at CU Boulder
    assignment earliest/latest graded date: The earliest/latest date when any grade was posted for this assignment for any student in Canvas
'''

In [ ]:
'''
Using these Canvas Data schema docs - Canvas Data Portal (inshosteddata.com) - 
write a SQL query (any dialect) that would tell you the average number of student enrollments 
per course for the enrollment term named “Fall 2023”. 
The aim of the query is to give a single number, such as 35.7, meaning Fall 2023 Canvas courses have an average of 35.7 students enrolled in them. 
We recognize that you cannot test or troubleshoot your query, so just do your best based on the documentation and be prepared to explain your thought process.

select (1.0*count(ef.enrollment_id)/count(distinct(ef.course_id))) as avg_enrollment
from enrollment_fact ef 
join enrollment_term_dim etd ON etd.id = ef.enrollment_term_id
where etd.name = "Fall 2023"
'''

In [ ]:
'''
Imagine you have been asked if there is a relationship between when in a semester an assignment is given and how long it takes to grade that assignment. '
Using the sample Canvas assignments data set, please tell us what the relationship is between (1) the number of days between an assignment’s due date and 
the start of the term and (2) the number of days between the assignment’s latest graded date and the assignment’s due date. Use any method you like to quantify the relationship (or lack of one). 
Be prepared to walk us through your method, explain why you chose the method you did, 
and why you do or do not think the relationship (or lack of one) is meaningful/significant.
'''

In [11]:
print(df.columns)
dfx = df[df.has_due_date == True].reset_index(drop=True)
dfx = dfx[dfx.assignment_due_date < datetime.strptime('2022-12-31','%Y-%m-%d')]
dfx = dfx[dfx.termstart_time_diff > 0]
print(df.shape)
print(dfx.shape)
dfx_box = dfx[(dfx.duedate_time_diff >= 0) & (dfx.duedate_time_diff <= 120) & (dfx.graded_time_diff >= 0) & (dfx.graded_time_diff <= 120)]

Index(['term', 'term_start_date', 'term_end_date', 'class_name',
       'assignment_name', 'assignment_type', 'assignment_posted_date',
       'assignment_due_date', 'assignment_latest_graded_date',
       'assignment_earliest_graded_date', 'due_Weekday', 'due_Day_Number',
       'graded_time_diff', 'duedate_time_diff', 'termstart_time_diff',
       'termendGDD_time_diff', 'subject', 'level', 'level2', 'has_due_date',
       'has_assignment_type'],
      dtype='object')
(47866, 21)
(28984, 21)


In [12]:
print(dfx_box.shape)
print(len(dfx_box)/len(df[df.has_due_date == True]))

(28255, 21)
0.9717636538726098


In [26]:
dfy=df[df.has_due_date == False].reset_index(drop=True)
print(dfy.shape)
dfy.head()

(18790, 21)


term term_start_date term_end_date     class_name     assignment_name  \
0  Fall 2022      2022-08-21    2022-12-13  CHEM 1113-300   Recitation Week 2   
1  Fall 2022      2022-08-21    2022-12-13  CHEM 1113-314   Recitation Week 2   
2  Fall 2022      2022-08-21    2022-12-13  CHEM 1113-300  Recitation Week 14   
3  Fall 2022      2022-08-21    2022-12-13  CHEM 1113-314  Recitation Week 14   
4  Fall 2022      2022-08-21    2022-12-13  CHEM 1113-300  Recitation Week 13   

  assignment_type assignment_posted_date assignment_due_date  \
0            none             2022-08-03                none   
1            none             2022-08-03                none   
2            none             2022-08-03                none   
3            none             2022-08-03                none   
4            none             2022-08-03                none   

  assignment_latest_graded_date assignment_earliest_graded_date  ...  \
0                    2022-12-12                      2022-09-06  ...   
1                    2022-09-12                      2022-09-09  ...   
2                    2022-12-14                      2022-12-05  ...   
3                    2022-12-08                      2022-12-06  ...   
4                    2022-12-09                      2022-11-28  ...   

  due_Day_Number graded_time_diff  duedate_time_diff  termstart_time_diff  \
0           None               97                NaN                  NaN   
1           None                3                NaN                  NaN   
2           None                9                NaN                  NaN   
3           None                2                NaN                  NaN   
4           None               11                NaN                  NaN   

   termendGDD_time_diff  subject level  level2 has_due_date  \
0                     1     CHEM  1000     300        False   
1                    92     CHEM  1000     314        False   
2                    -1     CHEM  1000     300        False   
3                     5     CHEM  1000     314        False   
4                     4     CHEM  1000     300        False   

   has_assignment_type  
0                False  
1                False  
2                False  
3                False  
4                False  

[5 rows x 21 columns]

In [ ]:
#Also, calculate durations from maybe assignment posted to 
# df['graded_time_diff'] = df.assignment_latest_graded_date - df.assignment_earliest_graded_date
# df['duedate_time_diff'] = df.assignment_latest_graded_date - df.assignment_due_date
# df['termstart_time_diff'] = df.assignment_due_date - df.term_start_date

In [97]:
fig = px.scatter(dfx, x="duedate_time_diff", y="termstart_time_diff", width=800, height=500, #trendline="ols", trendline_scope="overall",
                 color_discrete_sequence=px.colors.qualitative.Dark24,
                 color="termendGDD_time_diff",
                 title = 'Term End-Due Date vs Due Date-Term Start',
                 template = 'plotly_white',
                 log_x=False, log_y=False,           
                 labels={
                     "duedate_time_diff": "Days between latest graded date and due date",
                     "termstart_time_diff": "Days between due date and term start"
                 })
fig.update_traces(opacity=.1)
fig.show()

In [ ]:
'''
The far right edge are mistakes in entering the latest graded date.  
Almost of them are PHYS 1120, different sections - one exception!  There was a PSYC 1001 course that had a graded date about a year after the due date.
They all have a due date earlier than the assignment posted date
They are all homeworks
They all have the wrong year in the assignment last graded date
Many of them are off be an odd time like 1 month and 3 weeks less than the assignment posted date, so systematic and oddly incorrect
'''

In [15]:
dfx.term_start_date.value_counts()

2022-08-21    16656
2022-01-09    12328
Name: term_start_date, dtype: int64

In [ ]:
#dfx[(dfx.duedate_time_diff == 264)]
#dfx[(dfx.duedate_time_diff == 240)]
#dfx[(dfx.duedate_time_diff == 89) & (dfx.termstart_time_diff == 109)]
dfx[(dfx.duedate_time_diff == 0) & (dfx.termstart_time_diff == 193)]

In [ ]:
#2024-12-31 
dfx[(dfx.duedate_time_diff > 330) & (dfx.duedate_time_diff < 365)]

In [ ]:
max(dfx.term_end_date)

In [ ]:
#31 cases where assignment due date set into the next calendar
dfx[dfx.assignment_due_date > datetime.strptime('2022-12-31','%Y-%m-%d')]

In [18]:
fig = px.scatter(dfx, x="duedate_time_diff", y="graded_time_diff", width=800, height=500, #trendline="ols", trendline_scope="overall",
                 color_discrete_sequence=px.colors.qualitative.Dark24,
                 color='termstart_time_diff',
                 title = 'Term End-Due Date vs Latest-Earliest Graded Difference',
                 template = 'plotly_white',
                 log_x=False, log_y=False,           
                 labels={
                     "duedate_time_diff": "Latest graded date - due date (days)",
                     "graded_time_diff": "Days between earliest and latest graded date",
                     "termstart_time_diff":"Days between start of term and due date"
                 })
fig.update_traces(opacity=.1)
fig.show()

In [ ]:
'''
Main Pattern
1. 120x120 box
2. About 27.5% each of the left and bottom edges(55% total), about 45% elsewhere
3. Left edge is assignments that were due later in the semester and grades were done throughout, or, things that occured near or at/after semester end, like practicums.
4. Bottom edge
'''

In [24]:
fig = px.scatter(dfx_box, x="duedate_time_diff", y="graded_time_diff", width=800, height=500, 
                 color='termstart_time_diff',#trendline="ols", trendline_scope="overall",
                 color_discrete_sequence=px.colors.qualitative.Dark24,
                 title = 'Latest Graded Date-Due Date vs Latest-Earliest Graded Difference',
                 template = 'plotly_white',
                 log_x=False, log_y=False,           
                 labels={
                     "duedate_time_diff": "Latest graded date - due date (days)",
                     "graded_time_diff": "Latest - earliest graded date (days)",
                     "termstart_time_diff":"Due date - Start of term (days)"
                 })
fig.update_traces(opacity=.05)
fig.show()

In [36]:
print('Overall')
print(f'Overall Median GDD for df = {np.median(df.graded_time_diff)}')
print(f'Overall Median GDD for dfx = {np.median(dfx.graded_time_diff)}')
print(f'Overall Median GDD for dfx_box = {np.median(dfx_box.graded_time_diff)}')
print(f'Overall Mean GDD for df = {np.mean(df.graded_time_diff):0.3}')
print(f'Overall Mean GDD for dfx = {np.mean(dfx.graded_time_diff):0.3}')
print(f'Overall Mean GDD for dfx_box = {np.mean(dfx_box.graded_time_diff):0.3}')

print('')
print(f'Overall Median GDD for df = {np.median(df.graded_time_diff)}')
print(f'Overall Mean GDD for dfy = {np.mean(dfx_box.graded_time_diff):0.3}')

print('')

print('Left Edge')
print(f'Median GDD LeftEdge = {np.median(leftEdge.graded_time_diff)}')
print(f'Median DDD LeftEdge = {np.median(leftEdge.duedate_time_diff)}')
print(f'Mean GDD LeftEdge = {np.mean(leftEdge.graded_time_diff):0.3}')
print(f'Mean DDD LeftEdge = {np.mean(leftEdge.duedate_time_diff):0.3}')

print('')

print('Bottom Edge')
print(f'Median GDD BottomEdge = {np.median(bottomEdge.graded_time_diff)}')
print(f'Median DDD BottomEdge = {np.median(bottomEdge.duedate_time_diff)}')
print(f'Mean GDD BottomEdge = {np.mean(bottomEdge.graded_time_diff):0.3}')
print(f'Mean DDD BottomEdge = {np.mean(bottomEdge.duedate_time_diff):0.3}')

print('')

print('No Edge')
print(f'Median GDD NoEdge = {np.median(noEdge.graded_time_diff)}')
print(f'Median DDD NoEdge = {np.median(noEdge.duedate_time_diff)}')
print(f'Mean GDD NoEdge = {np.mean(noEdge.graded_time_diff):0.3}')
print(f'Mean DDD NoEdge = {np.mean(noEdge.duedate_time_diff):0.3}')


Overall
Overall Median GDD for df = 3.0
Overall Median GDD for dfx = 7.0
Overall Median GDD for dfx_box = 6.0
Overall Mean GDD for df = 17.3
Overall Mean GDD for dfx = 21.2
Overall Mean GDD for dfx_box = 17.6

Overall Median GDD for df = 3.0
Overall Mean GDD for dfy = 17.6

Left Edge
Median GDD LeftEdge = 5.0
Median DDD LeftEdge = 0.0
Mean GDD LeftEdge = 9.05
Mean DDD LeftEdge = 0.473

Bottom Edge
Median GDD BottomEdge = 0.0
Median DDD BottomEdge = 15.0
Mean GDD BottomEdge = 0.414
Mean DDD BottomEdge = 28.6

No Edge
Median GDD NoEdge = 21.0
Median DDD NoEdge = 24.0
Mean GDD NoEdge = 33.3
Mean DDD NoEdge = 34.1


In [28]:
#Data for point 2 above.
leftEdge = dfx_box[(dfx_box.graded_time_diff >=0) & (dfx_box.duedate_time_diff <= 1)]
len(leftEdge)/len(dfx_box)

0.27110245974163866

In [29]:
#left edge case
leftEdge[['duedate_time_diff','graded_time_diff','term_start_date','term_end_date','class_name',
          'assignment_name','assignment_due_date',
          'assignment_latest_graded_date','assignment_earliest_graded_date']][0:10]

duedate_time_diff  graded_time_diff term_start_date term_end_date  \
284                1.0                 0      2022-08-21    2022-12-13   
285                1.0                 0      2022-08-21    2022-12-13   
286                1.0                 0      2022-08-21    2022-12-13   
287                1.0                 0      2022-08-21    2022-12-13   
288                1.0                 0      2022-08-21    2022-12-13   
289                1.0                 0      2022-08-21    2022-12-13   
290                1.0                 0      2022-08-21    2022-12-13   
291                1.0                 0      2022-08-21    2022-12-13   
292                1.0                 0      2022-08-21    2022-12-13   
293                1.0                 0      2022-08-21    2022-12-13   

        class_name      assignment_name  assignment_due_date  \
284  CSCI 1300-300  Retake: practicum 1  2022-12-14 00:00:00   
285  CSCI 1300-306  Retake: practicum 1  2022-12-14 00:00:00   
286  CSCI 1300-308  Retake: practicum 1  2022-12-14 00:00:00   
287  CSCI 1300-307  Retake: practicum 1  2022-12-14 00:00:00   
288  CSCI 1300-200  Retake: practicum 1  2022-12-14 00:00:00   
289  CSCI 1300-203  Retake: practicum 1  2022-12-14 00:00:00   
290  CSCI 1300-304  Retake: practicum 1  2022-12-14 00:00:00   
291  CSCI 1300-101  Retake: practicum 1  2022-12-14 00:00:00   
292  CSCI 1300-100  Retake: practicum 1  2022-12-14 00:00:00   
293  CSCI 1300-206  Retake: practicum 1  2022-12-14 00:00:00   

    assignment_latest_graded_date assignment_earliest_graded_date  
284                    2022-12-15                      2022-12-15  
285                    2022-12-15                      2022-12-15  
286                    2022-12-15                      2022-12-15  
287                    2022-12-15                      2022-12-15  
288                    2022-12-15                      2022-12-15  
289                    2022-12-15                      2022-12-15  
290                    2022-12-15                      2022-12-15  
291                    2022-12-15                      2022-12-15  
292                    2022-12-15                      2022-12-15  
293                    2022-12-15                      2022-12-15

In [30]:
bottomEdge = dfx_box[(dfx_box.graded_time_diff <= 3) & (dfx_box.duedate_time_diff >1)]
len(bottomEdge)/len(dfx_box)

0.2779331091842152

In [31]:
bottomEdge[['term_start_date','term_end_date','class_name','assignment_name','assignment_due_date','assignment_latest_graded_date','assignment_earliest_graded_date']][0:10]

term_start_date term_end_date     class_name              assignment_name  \
75       2022-08-21    2022-12-13  APPM 1350-222                         HW 9   
77       2022-08-21    2022-12-13  APPM 1350-233                         HW 9   
120      2022-08-21    2022-12-13  APPM 1350-233                       Quiz 3   
191      2022-08-21    2022-12-13  APPM 1350-233                       Quiz 1   
203      2022-08-21    2022-12-13  ECON 2010-400  ASSESS Chapter 12B Homework   
204      2022-08-21    2022-12-13  ECON 2010-417  ASSESS Chapter 12B Homework   
207      2022-08-21    2022-12-13  MCDB 1150-001                   Final Exam   
212      2022-08-21    2022-12-13  APPM 1350-241                        HW 13   
213      2022-08-21    2022-12-13  APPM 1350-241                        HW 12   
232      2022-08-21    2022-12-13  APPM 1350-254                        HW 12   

     assignment_due_date assignment_latest_graded_date  \
75   2022-10-24 00:00:00                    2022-11-08   
77   2022-10-24 00:00:00                    2022-11-08   
120  2022-09-20 00:00:00                    2022-09-28   
191  2022-08-30 00:00:00                    2022-09-06   
203  2022-12-08 00:00:00                    2022-12-17   
204  2022-12-08 00:00:00                    2022-12-17   
207  2022-12-12 00:00:00                    2022-12-15   
212  2022-11-28 00:00:00                    2022-12-09   
213  2022-11-14 00:00:00                    2022-12-01   
232  2022-11-14 00:00:00                    2022-12-01   

    assignment_earliest_graded_date  
75                       2022-11-08  
77                       2022-11-08  
120                      2022-09-26  
191                      2022-09-05  
203                      2022-12-16  
204                      2022-12-16  
207                      2022-12-13  
212                      2022-12-07  
213                      2022-11-29  
232                      2022-11-29

In [32]:
(len(bottomEdge)/len(dfx_box)+len(leftEdge)/len(dfx_box))

0.5490355689258539

In [33]:
noEdge = dfx_box[(dfx_box.graded_time_diff > 3) & (dfx_box.duedate_time_diff >1)]
len(noEdge)/len(dfx_box)

0.4509644310741462

In [34]:
len(set.union(set(leftEdge.index),set(bottomEdge.index)))/len(dfx_box)

0.5490355689258538

In [35]:
1-(len(bottomEdge)/len(dfx_box)+len(leftEdge)/len(dfx_box))

0.4509644310741461

In [ ]:
longGDD = dfx[dfx.graded_time_diff > 300]

In [ ]:
longGDD[longGDD.]

In [ ]:
100*len(longGDD)/len(dfx)

In [ ]:
fig = px.scatter(dfx, x="termstart_time_diff", y="graded_time_diff", width=800, height=500, #trendline="ols", trendline_scope="overall",
                 color_discrete_sequence=px.colors.qualitative.Dark24,
                 title = 'Term End-Due Date vs Latest-Earliest Graded Difference',
                 template = 'plotly_white',
                 log_x=False, log_y=False,           
                 labels={
                     "duedate_time_diff": "Days between latest graded date and due date",
                     "graded_time_diff": "Days between due date and term start"
                 })
fig.update_traces(opacity=.1)
fig.show()

In [ ]:
dfx.term_end_date[20000] - dfx.term_start_date[20000]

In [ ]:
#115 days
dfx.term_end_date[20000]

In [ ]:
dfx[(dfx.duedate_time_diff == 131) & (dfx.graded_time_diff == 144)]

In [37]:
dfy.termstart_time_diff.value_counts()

Series([], Name: termstart_time_diff, dtype: int64)

In [66]:
dfy = dfy.sort_values(by=['termendGDD_time_diff','graded_time_diff'],ascending=False)
dfy_box = dfy[(dfy.graded_time_diff >= 0) & (dfy.graded_time_diff <= 120)].reset_index(drop=True)
dfy_box = dfy_box.sort_values(by=['termendGDD_time_diff','graded_time_diff'],ascending=False)

In [88]:
fig = px.scatter(dfy_box, x=dfy_box.index,y="graded_time_diff", width=800, height=500, #trendline="ols", trendline_scope="overall",
                 color_discrete_sequence=px.colors.qualitative.Dark24,
                 color='termendGDD_time_diff',
                 title = 'Latest-Earliest Graded Difference',
                 template = 'plotly_white',
                 log_x=False, log_y=False,           
                 labels={
                     "graded_time_diff": "Days between earliest and latest graded date",
                     "termendGDD_time_diff":"Term end - Latest graded date"
                 })
fig.add_vline(x=14900, line_dash="dot",
              opacity=0.9,
              annotation_text=" Semester End -> ", 
              annotation_position="top left"
             )
fig.update_traces(opacity=.3)
fig.update_traces(marker={'size': 7})
fig.update_xaxes(showticklabels=False,title='Increasing time in semester -->')
fig.show()

In [96]:
dfy = dfy.sort_values(by=['graded_time_diff','termendGDD_time_diff'],ascending=True)
dfy_box = dfy[(dfy.graded_time_diff >= 0) & (dfy.graded_time_diff <= 120)].reset_index(drop=True)
dfy_box = dfy_box.sort_values(by=['graded_time_diff','termendGDD_time_diff'],ascending=True)

fig = px.scatter(dfy_box, x=dfy_box.index,y="graded_time_diff", width=800, height=500, #trendline="ols", trendline_scope="overall",
                 color_discrete_sequence=px.colors.qualitative.Dark24,
                 color='termendGDD_time_diff',
                 title = 'Latest-Earliest Graded Difference',
                 template = 'plotly_white',
                 log_x=False, log_y=False,           
                 labels={
                     "graded_time_diff": "Days between earliest and latest graded date",
                     "termendGDD_time_diff":"Term end - Latest graded date"
                 })
fig.update_traces(opacity=.5)
fig.add_vline(x=13000, line_dash="dot",
              opacity=0.25,
              annotation_text=" Latest-earliest = 3 days", 
              annotation_position="top left"
             )

fig.update_traces(opacity=.3)
fig.update_traces(marker={'size': 7})
fig.update_xaxes(showticklabels=False,title='Increasing Latest-Earliest Graded Difference -->')

fig.show()

In [ ]:
YbottomEdge = dfy_box[dfy_box.graded_time_diff <= 3]
YnoEdge = dfy_box[dfy_box.graded_date_diff > 3]

In [ ]:
print(dfy_box.shape)
print(len(dfy_box)/len(df[df.has_due_date == False]))

In [ ]:
print(len(YbottomEdge)/len(dfy_box))

In [ ]:
print(len(dfx_box[dfx_box.graded_time_diff <= 3])/len(dfx_box))

In [ ]:
print('Bottom Edge')
print(f'Median GDD BottomEdge = {np.median(YbottomEdge.graded_time_diff)}')
print(f'Mean GDD BottomEdge = {np.mean(YbottomEdge.graded_time_diff):0.3}')

print('')

print('No Edge')
print(f'Median GDD NoEdge = {np.median(YnoEdge.graded_time_diff)}')
print(f'Mean GDD NoEdge = {np.mean(YnoEdge.graded_time_diff):0.3}')


In [ ]:
'''
Overall
Overall Median GDD for df = 3.0
Overall Median GDD for dfx = 7.0
Overall Median GDD for dfx_box = 6.0
Overall Mean GDD for df = 17.3
Overall Mean GDD for dfx = 21.2
Overall Mean GDD for dfx_box = 17.6

Overall Median GDD for df = 3.0
Overall Mean GDD for dfy = 17.6

Bottom Edge
Median GDD xBottomEdge = 0.0
Median GDD yBottomEdge = 0.0

Mean GDD xBottomEdge = 0.414
Mean GDD yBottomEdge = 0.21

No Edge
Median GDD xNoEdge = 21.0
Median GDD yNoEdge = 26.0

Mean GDD xNoEdge = 33.3
Mean GDD yNoEdge = 36.2
'''